In [1]:
#from google.colab import drive
#drive.mount('/content/drive')

In [2]:
import os

import numpy as np
import pandas as pd

In [3]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [4]:
#base_dir = '/content/drive/MyDrive/Colab Notebooks/DATA'

Importing all necessary data

In [5]:
marks = pd.read_csv('marks.csv', low_memory=False)

In [6]:
applicants = pd.read_csv('applicants.csv')

In [7]:
statuses = pd.read_csv('statuses.csv', low_memory=False)

In [8]:
ratings_1 = pd.read_csv('ratings.csv',
                        encoding='cp1251',
                        sep=';',
                        low_memory=False)

In [9]:
ratings_2 = pd.read_csv('ratings_2.csv')

---

In [10]:
# delete those lines where there are either no dates or no ratings
marks = marks.drop(
    marks[
        ((marks['FirstAttemptDate'].isnull())
        & (marks['FirstStrResult'] == 'нет оценки'))
        | (marks['FirstStrResult'] == 'нет оценки')
        | (marks['FirstStrResult'] == '-')
        ].index
    ).reset_index(drop=True)

In [11]:
# remove extra columns
try: marks = marks.drop(columns=['FiveScaleMark'])
except: pass
try: marks = marks.drop(columns=['FirstFiveScaleMark'])
except: pass
try: marks = marks.drop(columns=['LearnPeriod$D'])
except: pass
try: marks = marks.drop(columns=['LearnSubject$D'])
except: pass
try: marks = marks.drop(columns=['ProposalItem'])
except: pass
try: marks = marks.drop(columns=['ToDate'])
except: pass
try: marks = marks.drop(columns=['FromDate'])
except: pass

In [12]:
# filter data only for master's students
marks = marks[
    marks['Course$D'].isin(
        ['Магистратура 1 курс', 'Магистратура 2 курс', 'Магистратура 3 курс']
        )
    ]

In [13]:
# delete this column, as it is no longer needed
# (there is another column with course number)
try: marks = marks.drop(columns=['Course$D'])
except: pass

In [14]:
# additional filtering by masters
marks = marks[
    marks['StudentClass$D'].isin(
        ['Студент магистратуры', 'Иностранный студент']
        )
    ]

In [15]:
# fill in the gaps with zeros based on the number of retakes
marks.loc[:, 'RepassCount'] = marks['RepassCount'].fillna(0)

In [16]:
# output the number of unique values ​​in each column
for col in marks.columns:
  print(marks[col].value_counts(), '\n')

CS_new
8703941008     87
9665665768     87
8671269685     72
8485821271     72
6882274015     69
441440833      68
1270798009     68
7119240898     68
11654597725    67
448831384      66
8403979918     64
12198422686    63
119436589      63
467890         62
11631351124    62
12483490345    62
7132766689     62
4899666964     60
6467927992     58
1359926488     58
8281927312     58
5280427825     56
8252314078     56
9052912249     56
5980390246     55
6404060893     55
3135778150     54
7856069665     54
8686233334     54
1308017479     53
8704731283     53
7118879623     53
8667564220     52
454438825      52
1280602843     51
275647453      51
8403975385     51
9009577246     51
426861325      50
6285569422     50
1778754667     50
421286533      50
259623454      49
277536898      49
11766444031    49
11945400586    49
433638562      49
4948821616     49
1913984329     49
7866062500     48
8175870922     48
7131688228     48
249306301      48
271613023      48
1837009525     48
959

In [17]:
# convert date columns to the appropriate type
date_format = "%d.%m.%Y"
dates = ['FirstAttemptDate', 'ExamDate', 'LastDate',
         'RepassBeginDate', 'RepassEndDate']

for col in dates:
  marks[col] = pd.to_datetime(
      marks[col],
      errors='coerce'
      )

C:\Users\Олег\AppData\Local\Temp\ipykernel_14672\1340880263.py:7: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  marks[col] = pd.to_datetime(
C:\Users\Олег\AppData\Local\Temp\ipykernel_14672\1340880263.py:7: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  marks[col] = pd.to_datetime(
C:\Users\Олег\AppData\Local\Temp\ipykernel_14672\1340880263.py:7: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  marks[col] = pd.to_datetime(
C:\Users\Олег\AppData\Local\Temp\ipykernel_14672\1340880263.py:7: UserWarning: Could not infer format, so each element will be parsed individually, falling b

In [18]:
# fill the gaps with a value different from the data logic
marks.loc[:, 'FirstMissed'] = marks['FirstMissed'].fillna(2)

In [19]:
# fill empty grade values ​​with zeros
# (didn't show up for the exam - no grade)
condition_test_mark = marks['FirstStrResult'].isin(
    ['н/я', 'н/я (ув.)']) & marks['FirstTestMark'].isnull()

marks.loc[condition_test_mark, 'FirstTestMark'] = 0

condition_ten_scale_mark = marks['FirstStrResult'].isin(
    ['н/я', 'н/я (ув.)']) & marks['FirstTenScaleMark'].isnull()

marks.loc[condition_ten_scale_mark, 'FirstTenScaleMark'] = 0

In [20]:
# deleting extra observations where there were no marks
marks = marks.dropna(subset=['FirstTenScaleMark']).reset_index(drop=True)

In [21]:
# fill in empty values
marks.loc[:, 'Missed'] = marks.Missed.fillna(2)
marks.loc[:, 'TestMark'] = marks.TestMark.fillna(0)
marks.loc[:, 'TenScaleMark'] = marks.TenScaleMark.fillna(0)
marks.loc[:, 'SubjectType$D'] = marks['SubjectType$D'].fillna('-')
marks.loc[:, 'PlanCourse$N'] = marks['PlanCourse$N'].fillna('-')
marks.loc[:, 'LearnProgram$D'] = marks['LearnProgram$D'].fillna('-')
marks.loc[:, 'ControlType$D'] = marks['ControlType$D'].fillna('-')

In [22]:
# deleting observations without dates
marks = marks.dropna(subset=['LastDate']).reset_index(drop=True)

In [23]:
# remove uninformative columns with dates
marks = marks.drop(columns=['RepassBeginDate', 'RepassEndDate'])

---

In [24]:
# remove uninformative observations
applicants = applicants[~applicants.iloc[:, 11].isin(
    ['Зачислен кандидатом в магистратуру',
     'Отчислен по собственному желанию как неприступивший к занятиям'])]

applicants = applicants[applicants.iloc[:, 11].notna()]

In [25]:
# fill in empty values
cols = [4, 5, 11, 14, 15, 16, 17, 21]
for col in cols:
  applicants.iloc[:, col] = applicants.iloc[:, col].fillna('-')

applicants.iloc[:, 13] = applicants.iloc[:, 13].fillna(-1)
applicants.iloc[:, 19] = applicants.iloc[:, 19].fillna(-1)

In [26]:
# deleting extra column
applicants = applicants.drop(applicants.columns[18], axis=1)

---

In [27]:
# convert data type
statuses['FromDate'] = pd.to_datetime(statuses['FromDate'], errors='coerce')

C:\Users\Олег\AppData\Local\Temp\ipykernel_14672\1751529867.py:2: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  statuses['FromDate'] = pd.to_datetime(statuses['FromDate'], errors='coerce')


In [28]:
# remove all observations before 2018, since
# in the table with marks all data is from 2018 and after
cutoff_date = pd.to_datetime('2018-01-01')

statuses = statuses[statuses['FromDate'] >= cutoff_date]

statuses = statuses.reset_index(drop=True)

In [29]:
# combine different categories to reduce the number of final statuses
def group_inc_category(category):
    if category in ['Зачисление студента',
                    'Зачисление в магистратуру',
                    'Зачисление иностранного студента']:
        return 'Зачисление'
    elif category in ['Отчисление студента',
                      'Отчисление иностранного студента']:
        return 'Отчисление'
    elif category in ['Перевод на другой факультет',
                      'Перевод в рамках факультета']:
        return 'Перевод'
    elif category in ['Уход в академический отпуск',
                      'Допуск после академического отпуска']:
        return 'Академический отпуск'
    elif category == 'Восстановление отчисленного':
        return 'Восстановление'
    else:
        return 'Прочее'

statuses['IncCategory$D'] = statuses['IncCategory$D'].apply(
    group_inc_category
    )

In [30]:
# remove unnecessary observations
statuses = statuses[~statuses.iloc[:, 10].isin(['Зачисление студента'])]

In [31]:
# remove uninformative columns
columns_to_drop = [
    'BirthDate', 'FromDate', 'AdmOrdDate', 'AdmOrdClass$D', 'AdmCategory$D',
    'AdmReason$D', 'ToDate', 'IncOrdDate', 'PrevStatus$N', 'NextStatus$N',
    'HostelResident$N', 'Hostel$D', 'IndPlanReason$N', 'IndPlanDate',
    'IndPlanToDate', 'IndPlanStartPeriod$D', 'QuitReasonRef$N', 'Course$N',
    'QuitOrder$D', 'FormerGroup', 'VacationDate', 'City$D'
]

statuses = statuses.drop(columns=columns_to_drop)

In [32]:
# remove empty values
statuses = statuses.dropna(subset=['RegDepartment$D']).reset_index(drop=True)

In [33]:
# defining new categories
def map_income_reason(reason):
    if pd.isna(reason):
        return "Прочее"
    if reason in [
        "Зачислен в магистратуру по конкурсу",
        "Зачислен в магистратуру на основании договора",
        "Зачислен в магистратуру в рамках установленной Правительство8C34",
        "Зачислен в магистратуру на основании договора в рамках отдел1C1F",
        "Зачислен в магистратуру по целевому набору",
        "Зачислен в магистратуру переводом на основании договора",
        "Зачислен в магистратуру в порядке перевода из другого ВУЗа",
        "Зачислен кандидатом в магистратуру",
        "Зачислен кандидатом в магистратуру в порядке перевода из друA6A9",
        "Зачислен в магистратуру переводом"
    ]:
        return "Зачисление в магистратуру"
    elif reason in [
        "Зачислен как иностранный студент",
        "Зачислен по договору за счет средств НИУ ВШЭ по результатам 595D",
        "Зачислен по договору за счет средств НИУ ВШЭ (иностранные гр86DD",
        "Зачислен на основании договора",
        "Зачислен кандидатом в порядке перевода из другого ВУЗа"
    ]:
        return "Зачисление"
    elif reason in [
        "Отчислен иностранный студент",
        "Отчислен по собственному желанию",
        "Отчислен за академическую неуспеваемость",
        "Отчислен по результатам ГИА",
        "Отчислен в связи с несвоевременным представлением ВКР",
        "Отчислен за нарушение правил внутреннего распорядка",
        "Отчислен в связи с невыполнением условий договора",
        "Отчислен в связи с невыходом из академического отпуска",
        "Отчислен по собственному желанию как неприступивший к заняти1F48",
        "Отчислен в связи с переводом в другой ВУЗ",
        "Отчислен в связи с нарушением Правил внутреннего распорядка 1393",
        "Отчислен в связи со смертью",
        "Отчислен в связи с досрочным прекращением образовательных от7675"
    ]:
        return "Отчисление"
    elif reason in [
        "Предоставлен академический отпуск по семейным обстоятельствам",
        "Допущен к занятиям после академического отпуска",
        "Предоставлен академический отпуск по медицинским показаниям",
        "Предоставлен отпуск по уходу за ребёнком",
        "Предоставлен отпуск по беременности и родам",
        "Предоставлен академический отпуск в связи с прохождением слу7CDE"
    ]:
        return "Академический отпуск"
    elif reason in [
        "Переведен на другой факультет в связи с реорганизацией",
        "Переведен на другой факультет",
        "Переведен на другой факультет в связи с регорагизацией",
        "Изменил образовательную программу"
    ]:
        return "Перевод"
    elif reason in ["Восстановлен"]:
        return "Восстановление"
    else:
        return "Прочее"

statuses['IncomeReason$N'] = statuses['IncomeReason$N'].apply(map_income_reason)

print(statuses['IncomeReason$N'].value_counts())

IncomeReason$N
Зачисление в магистратуру    28637
Отчисление                    9611
Прочее                        5882
Зачисление                    5545
Академический отпуск          2849
Перевод                       2123
Восстановление                 627
Name: count, dtype: int64


In [34]:
# fill in empty values
statuses.loc[:, 'Speciality$D'] = statuses['Speciality$D'].fillna('-')
statuses.loc[:, 'Group$D'] = statuses['Group$D'].fillna('-')
statuses.loc[:, 'Region$D'] = statuses['Region$D'].fillna('-')
statuses.loc[:, 'Country$D'] = statuses['Country$D'].fillna('-')
statuses['AdmissionYear$N'].fillna(0, inplace=True)
statuses['AdmissionYear$N'] = statuses['AdmissionYear$N'].astype(int)

C:\Users\Олег\AppData\Local\Temp\ipykernel_14672\2122311418.py:6: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  statuses['AdmissionYear$N'].fillna(0, inplace=True)


---

In [35]:
# remove obviously unnecessary columns
columns_to_drop = [
    "period_1", "period_2", "period_3", "period_4", "period_5", "period_6",
    "period_7", "period_8", "Группа_1", "Группа_2", "Группа_3", "Группа_4",
    "Группа_5", "Группа_6", "Группа_7", "Группа_8", "КРсумма_1", "КРсумма_2",
    "КРсумма_3", "КРсумма_4", "КРсумма_5", "КРсумма_6", "КРсумма_7",
    "КРсумма_8", "Нормкоэф_1", "Нормкоэф_2", "Нормкоэф_3", "Нормкоэф_4",
    "Нормкоэф_5", "Нормкоэф_6", "Нормкоэф_7", "Нормкоэф_8", "Кредитов_1",
    "Кредитов_2", "Кредитов_3", "Кредитов_4", "Кредитов_5", "Кредитов_6",
    "Кредитов_7", "Кредитов_8", "Перцентиль_1", "Перцентиль_2", "Перцентиль_3",
    "Перцентиль_4", "Перцентиль_5", "Перцентиль_6", "Перцентиль_7",
    "Перцентиль_8", "МестоОП_1", "МестоОП_2", "МестоОП_3", "МестоОП_4",
    "МестоОП_5", "МестоОП_6", "МестоОП_7", "МестоОП_8", "МестоОПвсего_1",
    "МестоОПвсего_2", "МестоОПвсего_3", "МестоОПвсего_4", "МестоОПвсего_5",
    "МестоОПвсего_6", "МестоОПвсего_7", "МестоОПвсего_8", "МестоОПКурс_1",
    "МестоОПКурс_2", "МестоОПКурс_3", "МестоОПКурс_4", "МестоОПКурс_5",
    "МестоОПКурс_6", "МестоОПКурс_7", "МестоОПКурс_8", "МестоОПКурсвсего_1",
    "МестоОПКурсвсего_2", "МестоОПКурсвсего_3", "МестоОПКурсвсего_4",
    "МестоОПКурсвсего_5", "МестоОПКурсвсего_6", "МестоОПКурсвсего_7",
    "МестоОПКурсвсего_8", "Место_1", "Место_2", "Место_3", "Место_4",
    "Место_5", "Место_6", "Место_7", "Место_8", "Местовсего_1", "Местовсего_2",
    "Местовсего_3", "Местовсего_4", "Местовсего_5", "Местовсего_6",
    "Местовсего_7", "Местовсего_8", "КолВСЕГО_1", "КолВСЕГО_2", "КолВСЕГО_3",
    "КолВСЕГО_4", "КолВСЕГО_5", "КолВСЕГО_6", "КолВСЕГО_7", "КолВСЕГО_8",
    "КолПУСТО_1", "КолПУСТО_2", "КолПУСТО_3", "КолПУСТО_4", "КолПУСТО_5",
    "КолПУСТО_6", "КолПУСТО_7", "КолПУСТО_8", "КолФИЗРА_1", "КолФИЗРА_2",
    "КолФИЗРА_3", "КолФИЗРА_4", "КолФИЗРА_5", "КолФИЗРА_6", "КолФИЗРА_7",
    "КолФИЗРА_8", "КолПРОЕКТОВ_1", "КолПРОЕКТОВ_2", "КолПРОЕКТОВ_3",
    "КолПРОЕКТОВ_4", "КолПРОЕКТОВ_5", "КолПРОЕКТОВ_6", "КолПРОЕКТОВ_7",
    "КолПРОЕКТОВ_8", "Колпересдачпонеуважпричине_1",
    "Колпересдачпонеуважпричине_2", "Колпересдачпонеуважпричине_3",
    "Колпересдачпонеуважпричине_4", "Колпересдачпонеуважпричине_5",
    "Колпересдачпонеуважпричине_6", "Колпересдачпонеуважпричине_7",
    "Колпересдачпонеуважпричине_8", "Колпересдачпоуважпричине_1",
    "Колпересдачпоуважпричине_2", "Колпересдачпоуважпричине_3",
    "Колпересдачпоуважпричине_4", "Колпересдачпоуважпричине_5",
    "Колпересдачпоуважпричине_6", "Колпересдачпоуважпричине_7",
    "Колпересдачпоуважпричине_8"
]

ratings_1 = ratings_1.drop(columns=columns_to_drop)

In [36]:
# we use regular expressions to remove unnecessary characters
ratings_1 = ratings_1.replace(',', '.', regex=True)
ratings_1 = ratings_1.replace(r'^\s*$', np.nan, regex=True)

ratings_1 = ratings_1.astype(float)

In [37]:
# aggregate columns and remove unnecessary ones
columns_to_sum = [
    "КРсумманорм_1", "КРсумманорм_2", "КРсумманорм_3", "КРсумманорм_4",
    "КРсумманорм_5", "КРсумманорм_6", "КРсумманорм_7", "КРсумманорм_8"
]
ratings_1["КР_сумма"] = ratings_1[columns_to_sum].sum(axis=1)
ratings_1 = ratings_1.drop(columns=columns_to_sum)

columns_to_average = [
    "Средняяоценка_1", "Средняяоценка_2", "Средняяоценка_3", "Средняяоценка_4",
    "Средняяоценка_5", "Средняяоценка_6", "Средняяоценка_7", "Средняяоценка_8"
]
ratings_1["Средняя_оценка"] = ratings_1[columns_to_average].mean(axis=1)
ratings_1 = ratings_1.drop(columns=columns_to_average)

columns_not_passed = [
    "КолНЕСДАНО_1", "КолНЕСДАНО_2", "КолНЕСДАНО_3", "КолНЕСДАНО_4",
    "КолНЕСДАНО_5", "КолНЕСДАНО_6", "КолНЕСДАНО_7", "КолНЕСДАНО_8"
]

columns_passed = [
    "КолСДАНО_1", "КолСДАНО_2", "КолСДАНО_3", "КолСДАНО_4",
    "КолСДАНО_5", "КолСДАНО_6", "КолСДАНО_7", "КолСДАНО_8"
]

columns_fail = [
    "КолНЕУД_1", "КолНЕУД_2", "КолНЕУД_3", "КолНЕУД_4",
    "КолНЕУД_5", "КолНЕУД_6", "КолНЕУД_7", "КолНЕУД_8"
]

columns_satisfactory = [
    "КолУДОВЛ_1", "КолУДОВЛ_2", "КолУДОВЛ_3", "КолУДОВЛ_4",
    "КолУДОВЛ_5", "КолУДОВЛ_6", "КолУДОВЛ_7", "КолУДОВЛ_8"
]

columns_good = [
    "КолХОР_1", "КолХОР_2", "КолХОР_3", "КолХОР_4",
    "КолХОР_5", "КолХОР_6", "КолХОР_7", "КолХОР_8"
]

columns_excellent = [
    "КолОТЛ_1", "КолОТЛ_2", "КолОТЛ_3", "КолОТЛ_4",
    "КолОТЛ_5", "КолОТЛ_6", "КолОТЛ_7", "КолОТЛ_8"
]

ratings_1["Не_сдано"] = ratings_1[columns_not_passed].sum(axis=1)
ratings_1["Сдано"] = ratings_1[columns_passed].sum(axis=1)
ratings_1["Неуды"] = ratings_1[columns_fail].sum(axis=1)
ratings_1["Удовл"] = ratings_1[columns_satisfactory].sum(axis=1)
ratings_1["Хор"] = ratings_1[columns_good].sum(axis=1)
ratings_1["Отл"] = ratings_1[columns_excellent].sum(axis=1)

ratings_1 = ratings_1.drop(
    columns=columns_not_passed
    + columns_passed
    + columns_fail
    + columns_satisfactory
    + columns_good
    + columns_excellent
)

---

In [38]:
# we do all the same actions, since this data is 
# just a continuation of the previous ones by dates
ratings_2 = ratings_2.drop(columns=columns_to_drop)

In [39]:
ratings_2 = ratings_2.replace(',', '.', regex=True)
ratings_2 = ratings_2.replace(r'^\s*$', np.nan, regex=True)

ratings_2 = ratings_2.astype(float)

In [40]:
ratings_2["КР_сумма"] = ratings_2[columns_to_sum].sum(axis=1)
ratings_2 = ratings_2.drop(columns=columns_to_sum)

ratings_2["Средняя_оценка"] = ratings_2[columns_to_average].mean(axis=1)
ratings_2 = ratings_2.drop(columns=columns_to_average)

ratings_2["Не_сдано"] = ratings_2[columns_not_passed].sum(axis=1)
ratings_2["Сдано"] = ratings_2[columns_passed].sum(axis=1)
ratings_2["Неуды"] = ratings_2[columns_fail].sum(axis=1)
ratings_2["Удовл"] = ratings_2[columns_satisfactory].sum(axis=1)
ratings_2["Хор"] = ratings_2[columns_good].sum(axis=1)
ratings_2["Отл"] = ratings_2[columns_excellent].sum(axis=1)

ratings_2 = ratings_2.drop(
    columns=columns_not_passed
    + columns_passed
    + columns_fail
    + columns_satisfactory
    + columns_good
    + columns_excellent
)

---

In [41]:
# merge rating tables
ratings = pd.concat([ratings_1, ratings_2], ignore_index=True)

In [42]:
# fill in empty values
marks.loc[:, 'LearnProgram$D'] = marks['LearnProgram$D'].fillna('-')
ratings = ratings.fillna(-1)

---

In [43]:
# merge all tables by student ID (CS_new)
sm = pd.merge(statuses, marks, on='CS_new', how='left').dropna()
sma = pd.merge(sm, applicants, on='CS_new', how='left').dropna()
data = pd.merge(sma, ratings, on='CS_new', how='left').dropna()

In [44]:
# save the received data for using it in ML models
data.to_csv(os.path.join(#base_dir, 
                         'data.csv'), index=False)